# Day 3 - Conversational AI - aka Chatbot!

In [40]:
# imports

import os
import requests
from bs4 import BeautifulSoup
from typing import List
from dotenv import load_dotenv
from openai import OpenAI
import google.generativeai
# import anthropic
import gradio as gr

In [41]:
# Load environment variables in a file called .env

load_dotenv()
os.environ['GOOGLE_API_KEY'] = os.getenv('GOOGLE_API_KEY', 'your-key-if-not-using-env')

In [3]:
google.generativeai.configure()

In [4]:
system_message = "You are a helpful assistant"

In [5]:
system_message = "You are an assistant that is great at telling jokes"
user_prompt = "Tell a light-hearted joke for an audience of Data Scientists"

prompts = [
    {"role": "system", "content": system_message},
    {"role": "user", "content": user_prompt}
  ]

# The API for Gemini has a slightly different structure.
# I've heard that on some PCs, this Gemini code causes the Kernel to crash.
# If that happens to you, please skip this cell and use the next cell instead - an alternative approach.

gemini = google.generativeai.GenerativeModel(
    model_name='gemini-1.5-flash',
    system_instruction=system_message
)
response = gemini.generate_content(user_prompt)
print(response.text)

Why was the Data Scientist sad?  

Because they didn't get any arrays!



In [7]:
import google.generativeai as genai

model = genai.GenerativeModel('gemini-1.5-flash')

In [8]:
chat = model.start_chat(history=[])
response = chat.send_message('Hello! My name is Shardul.')
print(response.text)

Hello Shardul! It's nice to meet you.  How can I help you today?



In [9]:
response = chat.send_message('Can you tell something interesting about star wars?')
print(response.text)

Did you know that the iconic lightsaber fight choreography in Star Wars was heavily influenced by Japanese samurai sword fighting styles?  Specifically, the movements and stances of the Jedi and Sith were inspired by kendo and other forms of Japanese martial arts.  This gives the lightsaber battles a unique elegance and deadly precision that sets them apart from typical sword fights in other films.



In [10]:
response = chat.send_message('Do you remember what my name is?')
print(response.text)

Yes, your name is Shardul.



In [34]:
chat.history

[parts {
   text: "Hello! My name is Shardul."
 }
 role: "user",
 parts {
   text: "Hello Shardul!  It\'s nice to meet you. How can I help you today?\n"
 }
 role: "model",
 parts {
   text: "Can you tell something interesting about star wars?"
 }
 role: "user",
 parts {
   text: "One interesting fact about Star Wars is that the iconic lightsaber sound effect was created by recording the hum of a broken-down projector.  The sound designer, Ben Burtt, combined that with the sound of a television\'s static to create the distinctive whoosh and hum we all know and love.  It\'s a perfect example of how seemingly mundane sounds can be creatively repurposed to create iconic elements of a beloved franchise.\n"
 }
 role: "model",
 parts {
   text: "Do you remember what my name is?"
 }
 role: "user",
 parts {
   text: "Yes, your name is Shardul.\n"
 }
 role: "model"]

# Please read this! A change from the video:

In the video, I explain how we now need to write a function called:

`chat(message, history)`

Which expects to receive `history` in a particular format, which we need to map to the OpenAI format before we call OpenAI:

```
[
    {"role": "system", "content": "system message here"},
    {"role": "user", "content": "first user prompt here"},
    {"role": "assistant", "content": "the assistant's response"},
    {"role": "user", "content": "the new user prompt"},
]
```

But Gradio has been upgraded! Now it will pass in `history` in the exact OpenAI format, perfect for us to send straight to OpenAI.

So our work just got easier!

We will write a function `chat(message, history)` where:  
**message** is the prompt to use  
**history** is the past conversation, in OpenAI format  

We will combine the system message, history and latest message, then call OpenAI.

In [6]:
def chat(message, history):
    relevant_system_message = system_message
    if 'belt' in message:
        relevant_system_message += " The store does not sell belts; if you are asked for belts, be sure to point out other items on sale."
    
    messages = [{"role": "system", "content": relevant_system_message}] + history + [{"role": "user", "content": message}]

    stream = gemini.generate_content(message, safety_settings=[
        {"category": "HARM_CATEGORY_DANGEROUS_CONTENT", "threshold": "BLOCK_NONE"},
        {"category": "HARM_CATEGORY_SEXUALLY_EXPLICIT", "threshold": "BLOCK_NONE"},
        {"category": "HARM_CATEGORY_HATE_SPEECH", "threshold": "BLOCK_NONE"},
        {"category": "HARM_CATEGORY_HARASSMENT", "threshold": "BLOCK_NONE"}], stream=True)

    response = ""
    for chunk in stream:
        print(chunk)  # Print the chunk to understand its structure
        # Adjust the following line based on the actual structure of the chunk
        response += chunk.get('content', '') or ''
        yield response

In [11]:
chat_model = genai.GenerativeModel('gemini-1.5-flash')
chat = chat_model.start_chat()

msg = "what is gen ai"
stream = chat.send_message(msg, stream=True)
# print("Response:", stream.text)
for chunk in stream:
    print(chunk.text)


Gen
 AI, short for **Generative AI**, refers to a type of artificial intelligence
 that can create new content, rather than just analyzing or classifying existing data.  
This content can take many forms, including:

* **Text:**  Writing stories, articles, summaries, poems, code, scripts, etc.  Examples
 include ChatGPT, Bard, and Jasper.
* **Images:** Generating realistic or stylized images from text descriptions (prompts). Examples include DALL-E 
2, Midjourney, and Stable Diffusion.
* **Audio:** Creating music, sound effects, and voiceovers.  Examples include Amper Music and Jukebox.
* **Video:** Generating short video clips.  This is a
 rapidly developing area.
* **3D models:** Creating three-dimensional objects and scenes.

Gen AI achieves this by learning patterns and structures from massive datasets and then using this knowledge to generate new, similar but unique outputs.  The
 underlying techniques often involve deep learning models, particularly those based on neural networks

In [44]:
import time

chat = model.start_chat(history=[])

# Transform Gradio history to Gemini format
def transform_history(history):
    new_history = []
    for chat in history:
        new_history.append({"parts": [{"text": chat[0]}], "role": "user"})
        new_history.append({"parts": [{"text": chat[1]}], "role": "model"})
    return new_history

def response(message, history):
    global chat
    # The history will be the same as in Gradio, the 'Undo' and 'Clear' buttons will work correctly.
    chat.history = transform_history(history)
    response = chat.send_message(message)
    response.resolve()

    # Each character of the answer is displayed
    for i in range(len(response.text)):
        time.sleep(0.01)
        yield response.text[: i+1]

gr.ChatInterface(response,
                 textbox=gr.Textbox(placeholder="Question to Gemini")).launch(debug=True)

/opt/homebrew/Caskroom/miniconda/base/envs/llms/lib/python3.11/site-packages/gradio/components/chatbot.py:248: UserWarning: The 'tuples' format for chatbot messages is deprecated and will be removed in a future version of Gradio. Please set type='messages' instead, which uses openai-style 'role' and 'content' keys.
  warnings.warn(


* Running on local URL:  http://127.0.0.1:7870

To create a public link, set `share=True` in `launch()`.


Keyboard interruption in main thread... closing server.


<table style="margin: 0; text-align: left;">
    <tr>
        <td style="width: 150px; height: 150px; vertical-align: middle;">
            <img src="../business.jpg" width="150" height="150" style="display: block;" />
        </td>
        <td>
            <h2 style="color:#181;">Business Applications</h2>
            <span style="color:#181;">Conversational Assistants are of course a hugely common use case for Gen AI, and the latest frontier models are remarkably good at nuanced conversation. And Gradio makes it easy to have a user interface. Another crucial skill we covered is how to use prompting to provide context, information and examples.
<br/><br/>
Consider how you could apply an AI Assistant to your business, and make yourself a prototype. Use the system prompt to give context on your business, and set the tone for the LLM.</span>
        </td>
    </tr>
</table>